In [1]:
# Basic packages
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

# For Text processing
import string
import re
import warnings
warnings.filterwarnings('ignore')

# Install and import nltk and upprade if necessary libraries
%pip install nltk
import nltk
%pip install --upgrade pandas
%pip install openpyxl --upgrade


[notice] A new release of pip is available: 23.2.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.Requirement already satisfied: nltk in c:\users\tcolt\appdata\local\programs\python\python312\lib\site-packages (3.9.1)

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.2.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
# After reading the xsl file we find 4 missing values in the column 'Content'
df = pd.read_excel('df_complete_cleansing.xlsx')
df.head()
df.isna().sum()
  

SenderID             0
ReceiverID           0
ActionType           0
NegoOutcome          0
Content              4
Content_Length       0
Sentence_Count       0
Word_Count_nltk      0
NegoOutcomeLabel     0
Sentiment            0
SentimentCategory    0
dtype: int64

In [3]:
# Calculate the cumulative length of each exchanged message
df['Negotiation_Content_Length_sum'] = df.groupby(['SenderID', 'ReceiverID'])['Content_Length'].cumsum()

# Display df
#df

In [4]:
# Initialize a new column for negotiation length
df['Negotiation_Length'] = 0

# Function to calculate negotiation length
def calculate_negotiation_length(group):
    length = 0
    for i, row in group.iterrows():
        length += 1
        df.at[i, 'Negotiation_Length'] = length
        if row['ActionType'] in ['FinalAccept', 'FinalReject']:
            break

# Apply the function to each group of SenderID and ReceiverID
df.groupby(['SenderID', 'ReceiverID']).apply(calculate_negotiation_length)

# Display the DataFrame for verification focus on cell 6-7
#df.head(30)

Empty DataFrame
Columns: []
Index: []

SenderID 70 sent two counteroffers one after another is this an error in the system or is it possible since in the end he has a total of 8 sent messages and receiver 69 only 6. We will check if the sender id and receiver id follow the strict order of being a b a b instead of a a b a b a b b a. Cell 6 - 7 example.

In [5]:
import pandas as pd

# Count rows with missing values
na_rows = df[df['Content'].isna()]
print(na_rows)

      SenderID  ReceiverID    ActionType  NegoOutcome Content  Content_Length  \
552       2057        2058   FinalAccept  FinalAccept     NaN              29   
857       3457        3458  Counteroffer  FinalAccept     NaN               1   
1247       103         104         Offer  FinalAccept     NaN               8   
1404       133         134   FinalReject  FinalReject     NaN               1   

      Sentence_Count  Word_Count_nltk  NegoOutcomeLabel  Sentiment  \
552                1                5                 1        1.0   
857                1                1                 1        0.0   
1247               1                3                 1        0.5   
1404               1                1                 0        0.0   

     SentimentCategory  Negotiation_Content_Length_sum  Negotiation_Length  
552           Positive                            1367                   3  
857            Neutral                               1                   1  
1247        

In [6]:
import pandas as pd

# Remove rows with NaN in Content
df = df.dropna(subset=['Content'])

# Remove rows with empty strings or insignificant content in Content
def is_insignificant_content(content):
    return content.strip() == '' or content.strip() == '.' or len(content.split()) == 1

df = df[~df['Content'].apply(is_insignificant_content)]

# Validate Content Length (optional, if Content_Length column is used)
df['Content_Length'] = df['Content'].apply(len)

## Word Embeddings

In [7]:
#%pip install scipy==1.12

In [8]:
import nltk
#nltk.download('vader_lexicon')
nltk.download("word2vec_sample")

[nltk_data] Downloading package word2vec_sample to
[nltk_data]     C:\Users\TColt/nltk_data...
[nltk_data]   Package word2vec_sample is already up-to-date!


True

In [9]:
#%pip install gensim

In [10]:
import gensim
from nltk.data import find

word2vec_sample = str(find('models/word2vec_sample/pruned.word2vec.txt'))
pre_w2v_model = gensim.models.KeyedVectors.load_word2vec_format(word2vec_sample, binary=False)

In [11]:
len(pre_w2v_model.key_to_index)

43981

In [12]:
len(pre_w2v_model['negotiation'])

300

In [13]:
pre_w2v_model.most_similar(positive=["negotiation"], topn=20)

[('negotiations', 0.8168568015098572),
 ('negotiating', 0.7531847357749939),
 ('bargaining', 0.6434566378593445),
 ('negotiate', 0.6341554522514343),
 ('negotiated', 0.6292652487754822),
 ('talks', 0.6133744716644287),
 ('discussions', 0.6095365881919861),
 ('dialogue', 0.5417248606681824),
 ('haggling', 0.5341888070106506),
 ('agreement', 0.501986026763916),
 ('impasse', 0.4880932867527008),
 ('consultations', 0.4769951105117798),
 ('discussion', 0.4654763638973236),
 ('compromise', 0.4547061026096344),
 ('Discussions', 0.4485512673854828),
 ('brinkmanship', 0.44761836528778076),
 ('agreements', 0.4455186426639557),
 ('ratification', 0.4414721131324768),
 ('preconditions', 0.435526579618454),
 ('tripartite', 0.4344906210899353)]

In [14]:
pre_w2v_model.most_similar(positive=["negotiation"], negative=["agreement"], topn=10)

[('diplomacy', 0.323906272649765),
 ('dialogue', 0.29187703132629395),
 ('Interviewing', 0.28622379899024963),
 ('politicking', 0.28376883268356323),
 ('tactful', 0.2724672555923462),
 ('debates', 0.2721523642539978),
 ('bargaining', 0.2721068263053894),
 ('negotiations', 0.270591139793396),
 ('circumlocution', 0.2700679302215576),
 ('brinkmanship', 0.2678378224372864)]

In [15]:
print(pre_w2v_model)

KeyedVectors<vector_size=300, 43981 keys>


In [16]:
pre_w2v_model["negotiation"]

array([ 0.00503933,  0.0736899 , -0.0289142 ,  0.0624547 ,  0.0555153 ,
       -0.00116173,  0.0282533 , -0.0617938 ,  0.0565066 ,  0.0799685 ,
       -0.105743  ,  0.0134658 , -0.0305665 ,  0.0114005 , -0.107065  ,
        0.0806294 ,  0.1183    ,  0.00462627,  0.0256097 , -0.0156963 ,
        0.00078481,  0.067081  ,  0.00380015,  0.0852556 ,  0.0328796 ,
        0.0591502 , -0.109709  , -0.073029  ,  0.00805467, -0.044941  ,
        0.00305665, -0.0213139 , -0.0421321 ,  0.0456018 ,  0.0859165 ,
        0.0627852 , -0.00082612,  0.00636113,  0.0684028 , -0.148041  ,
        0.041306  ,  0.0391581 , -0.0366797 ,  0.0156137 , -0.15465   ,
        0.0105743 ,  0.00328383,  0.0137962 , -0.136145  ,  0.0845947 ,
       -0.00850904, -0.00950039, -0.0489063 , -0.035358  , -0.016605  ,
        0.0342014 ,  0.0472541 ,  0.00570023,  0.0614634 ,  0.041306  ,
       -0.142754  ,  0.0555153 , -0.0290794 ,  0.1031    ,  0.0138788 ,
        0.0829425 ,  0.03321   ,  0.0345318 ,  0.027262  , -0.11

## Self Trained embeddings

In [17]:
df['Content']

0       hope well management company agreed building f...
1       reaching mei apologize slight delay getting ba...
2       r kind response need hurry guess face daily fi...
3       swift reply read set proposal discussed collea...
4       proposal effort far seems getting close resolv...
                              ...                        
2327    latest offer point completely let u take corpo...
2328    much latest offer happy could already reached ...
2329    meyer fast answer happy found solution issue n...
2330    still interested coming joint result neverthel...
2331    sorry accept less understand argument like las...
Name: Content, Length: 2324, dtype: object

In [18]:
nego_message_data = df["Content"]
df_nego_message_data = pd.DataFrame(nego_message_data)
df_nego_message_data

Content
0     hope well management company agreed building f...
1     reaching mei apologize slight delay getting ba...
2     r kind response need hurry guess face daily fi...
3     swift reply read set proposal discussed collea...
4     proposal effort far seems getting close resolv...
...                                                 ...
2327  latest offer point completely let u take corpo...
2328  much latest offer happy could already reached ...
2329  meyer fast answer happy found solution issue n...
2330  still interested coming joint result neverthel...
2331  sorry accept less understand argument like las...

[2324 rows x 1 columns]

In [19]:
import nltk
from nltk.tokenize import word_tokenize

# Download the "punkt" model if not already preinstalled as before ind pre processing
nltk.download('punkt_tab')


df_nego_message_data['Tolenized_Content'] = df_nego_message_data['Content'].apply(word_tokenize)
df_nego_message_data

[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\TColt/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


Content  \
0     hope well management company agreed building f...   
1     reaching mei apologize slight delay getting ba...   
2     r kind response need hurry guess face daily fi...   
3     swift reply read set proposal discussed collea...   
4     proposal effort far seems getting close resolv...   
...                                                 ...   
2327  latest offer point completely let u take corpo...   
2328  much latest offer happy could already reached ...   
2329  meyer fast answer happy found solution issue n...   
2330  still interested coming joint result neverthel...   
2331  sorry accept less understand argument like las...   

                                      Tolenized_Content  
0     [hope, well, management, company, agreed, buil...  
1     [reaching, mei, apologize, slight, delay, gett...  
2     [r, kind, response, need, hurry, guess, face, ...  
3     [swift, reply, read, set, proposal, discussed,...  
4     [proposal, effort, far, seems, getting, close,...  
...                                                 ...  
2327  [latest, offer, point, completely, let, u, tak...  
2328  [much, latest, offer, happy, could, already, r...  
2329  [meyer, fast, answer, happy, found, solution, ...  
2330  [still, interested, coming, joint, result, nev...  
2331  [sorry, accept, less, understand, argument, li...  

[2324 rows x 2 columns]

In [20]:
sentences = df_nego_message_data['Tolenized_Content'].tolist()
sentences

[['hope',
  'well',
  'management',
  'company',
  'agreed',
  'building',
  'fruitful',
  'partnership',
  'face',
  'upcoming',
  'disruption',
  'market',
  'best',
  'innovation',
  'green',
  'spirit',
  'would',
  'like',
  'introduce',
  'nasa',
  'nova',
  'reaching',
  'tighten',
  'general',
  'term',
  'harm',
  'ag',
  'established',
  'round',
  'discussion',
  'far',
  'please',
  'find',
  'attached',
  'proposal',
  'open',
  'issue',
  'joint',
  'venture',
  'would',
  'like',
  'explain',
  'following',
  'director',
  'would',
  'like',
  'address',
  'unsolved',
  'issue',
  'number',
  'director',
  'sent',
  'since',
  'agreed',
  'decisionmaking',
  'committee',
  'consisting',
  'member',
  'simple',
  'majority',
  'power',
  'strongly',
  'suggest',
  'dividing',
  'seat',
  'svn',
  'tech',
  'would',
  'able',
  'deal',
  'local',
  'authority',
  'partner',
  'successfully',
  'using',
  'strong',
  'local',
  'network',
  'relationship',
  'engineer',
  '

In [21]:
from gensim.models.word2vec import Word2Vec

ourfirst_w2v_model = Word2Vec(sentences=sentences, vector_size=300, window=5, min_count=1, workers=4)
ourfirst_w2v_model.save("ourfirst_w2v_model")
ourfirst_w2v_model

In [22]:
example_vector = ourfirst_w2v_model.wv['accept']
print(example_vector)

[-1.01015568e-01  7.34068155e-01  4.79136080e-01  2.26712093e-01
  1.60581559e-01 -3.88285309e-01  4.09952819e-01  9.53504443e-01
 -5.91709502e-02 -2.06627175e-01  3.84571791e-01  9.29186940e-02
 -1.62139013e-01  2.78533280e-01  3.77197415e-01  9.97309759e-03
  3.73282731e-01 -8.04476663e-02  6.61612526e-02  1.01796180e-01
 -4.92380448e-02 -3.86999995e-01  4.96698350e-01 -2.12535307e-01
  4.80700016e-01 -2.34457165e-01  1.74132183e-01  1.45012125e-01
  5.09898365e-03 -6.53881431e-01  9.54635367e-02 -6.53492689e-01
 -1.48120493e-01  1.30539283e-01  2.49402717e-01  1.65522575e-01
  5.01671731e-01  4.80475537e-02  1.64536908e-01  1.32337380e-02
 -7.17503950e-02 -1.44933045e-01  4.86567765e-01 -2.02701539e-01
  3.57413411e-01  6.61572158e-01  2.17081353e-01  3.74492019e-01
 -3.52116860e-02  5.52310467e-01 -3.20813395e-02  6.13420159e-02
 -5.16728878e-01 -2.13607699e-01 -4.55250800e-01  1.19369552e-01
  2.41447031e-01 -1.20815359e-01  1.37981072e-01 -1.22085154e-01
 -1.70117691e-01  2.89342

In [23]:
similartoaccept = ourfirst_w2v_model.wv.most_similar('accept', topn=10)
similartoaccept

[('last', 0.9472310543060303),
 ('offer', 0.9322761297225952),
 ('agree', 0.9049420356750488),
 ('topic', 0.8977027535438538),
 ('change', 0.895517885684967),
 ('unfortunately', 0.8902018070220947),
 ('following', 0.8834875822067261),
 ('proposal', 0.8813301920890808),
 ('point', 0.8762786388397217),
 ('discus', 0.8729709386825562)]

## LSTM-Preprocessing

Install all the necessary packages to use them for the deep learning algorithms.

In [24]:
#%pip install keras

In [25]:
#%pip install tensorflow

In [26]:
#%pip install Keras-Preprocessing

In [27]:
#%pip install tensorflow-text

In [28]:
from tensorflow.keras.preprocessing.text import Tokenizer
from keras.utils import pad_sequences
from keras.models import Sequential
from keras.layers import Embedding, LSTM, Dense

In [29]:
sentences

[['hope',
  'well',
  'management',
  'company',
  'agreed',
  'building',
  'fruitful',
  'partnership',
  'face',
  'upcoming',
  'disruption',
  'market',
  'best',
  'innovation',
  'green',
  'spirit',
  'would',
  'like',
  'introduce',
  'nasa',
  'nova',
  'reaching',
  'tighten',
  'general',
  'term',
  'harm',
  'ag',
  'established',
  'round',
  'discussion',
  'far',
  'please',
  'find',
  'attached',
  'proposal',
  'open',
  'issue',
  'joint',
  'venture',
  'would',
  'like',
  'explain',
  'following',
  'director',
  'would',
  'like',
  'address',
  'unsolved',
  'issue',
  'number',
  'director',
  'sent',
  'since',
  'agreed',
  'decisionmaking',
  'committee',
  'consisting',
  'member',
  'simple',
  'majority',
  'power',
  'strongly',
  'suggest',
  'dividing',
  'seat',
  'svn',
  'tech',
  'would',
  'able',
  'deal',
  'local',
  'authority',
  'partner',
  'successfully',
  'using',
  'strong',
  'local',
  'network',
  'relationship',
  'engineer',
  '

In [30]:
# self-trained W2V
ourfirst_w2v_model

#pre-trained Google pruned W2V
pre_w2v_model

In [31]:
# See how big the vocabulary is for the self-trained W2V model
vocab_size = len(ourfirst_w2v_model.wv.index_to_key)+1  # new method indextokey
embedding_dim = ourfirst_w2v_model.wv.vector_size

In [32]:
vocab_size, embedding_dim

(6626, 300)

In [33]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(sentences)
word_index = tokenizer.word_index
word_index

{'would': 1,
 'offer': 2,
 'think': 3,
 'u': 4,
 'event': 5,
 'also': 6,
 'worker': 7,
 'like': 8,
 'issue': 9,
 'conference': 10,
 'agree': 11,
 'important': 12,
 'sponsor': 13,
 'local': 14,
 'want': 15,
 'additional': 16,
 'company': 17,
 'point': 18,
 'good': 19,
 'harm': 20,
 'music': 21,
 'best': 22,
 'make': 23,
 'compensation': 24,
 'therefore': 25,
 'could': 26,
 'international': 27,
 'time': 28,
 'engineer': 29,
 'hope': 30,
 'really': 31,
 'board': 32,
 'know': 33,
 'happy': 34,
 'since': 35,
 'slovenia': 36,
 'joint': 37,
 'common': 38,
 'isa': 39,
 'act': 40,
 'speech': 41,
 'director': 42,
 'nt': 43,
 'court': 44,
 'date': 45,
 'member': 46,
 'already': 47,
 'jurisdiction': 48,
 'venture': 49,
 'course': 50,
 'art': 51,
 'forward': 52,
 'future': 53,
 'take': 54,
 'get': 55,
 'accept': 56,
 'understand': 57,
 'negotiation': 58,
 'payment': 59,
 'catering': 60,
 'inc': 61,
 'ag': 62,
 'option': 63,
 'agreement': 64,
 'well': 65,
 'find': 66,
 'need': 67,
 'meal': 68,
 'reg

In [34]:
sequences = tokenizer.texts_to_sequences(sentences)
padded_sequences = pad_sequences(sequences, maxlen=5,padding='post') # LSTM needs fixed length sequences (gleiche Länge)
padded_sequences

array([[  52,  254,  159,  111,   83],
       [ 313,  157,   76,   52,  229],
       [  76,   52,  254,  111,   83],
       ...,
       [   5,  158,   52,  149, 4237],
       [ 280,   76,   52,  254, 4237],
       [ 165,  209,  430,  187,   30]])

In [35]:
embedding_matrix = np.zeros((vocab_size, embedding_dim))

for word, i in word_index.items():
    if word in ourfirst_w2v_model.wv:
        embedding_matrix[i] = ourfirst_w2v_model.wv[word]


embedding_matrix 

array([[ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [-1.09910354e-01, -1.40922400e-03,  3.07527483e-01, ...,
        -1.45266876e-01,  4.03917789e-01, -9.74634811e-02],
       [-2.56412309e-02,  6.69807553e-01,  4.33990389e-01, ...,
         7.33454153e-02,  5.22515401e-02, -2.91325927e-01],
       ...,
       [-5.77700615e-04,  3.50640941e-04,  2.78865045e-04, ...,
        -1.05562585e-03,  3.60096805e-03,  3.51778057e-04],
       [ 7.06433132e-03,  7.96440709e-03, -8.95551313e-03, ...,
        -1.11379400e-02,  2.29145540e-03,  2.95150699e-03],
       [-5.20155416e-04,  7.40152737e-03, -6.16696023e-04, ...,
        -1.09173171e-02,  5.83065581e-03, -3.23772989e-03]])

In [36]:
#Create test and train split
from sklearn.model_selection import train_test_split

X = padded_sequences
y = df['NegoOutcomeLabel']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)



## LSTM-Training

In [37]:
import tensorflow as tf
from keras.layers import Dropout

max_len = 10  # max length of a sentence


# 3 layers: Embedding, LSTM, Dense # use TRUE in trainable to train the embedding layer around 2,96 Mio parameters to train
model = Sequential([
    Embedding(input_dim=vocab_size,
              output_dim=embedding_dim,
              weights=[embedding_matrix],
              input_length=max_len,
              trainable=True),  # Embeddings trainierbar
    LSTM(128, return_sequences=False, dropout=0.3, recurrent_dropout=0.3),  # Anpassung je nach Bedarf
    Dropout(0.5),  # Dropout layer for regularization
    Dense(32, activation='relu'),  # Fully connected layer
    Dropout(0.5),  # Dropout layer for regularization
    Dense(1, activation='sigmoid')  # Binäre Klassifikation
])

In [38]:
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding (Embedding)           │ ?                      │     1,987,800 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm (LSTM)                     │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ ?                      │   0 (unbuilt) │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 1,987,800 (7.58 MB)

 Trainable params: 1,987,800 (7.58 MB)

 Non-trainable params: 0 (0.00 B)

In [39]:
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

In [40]:
history = model.fit(X, np.array(df['NegoOutcomeLabel']), epochs=20, batch_size=2, validation_split=0.2)

Epoch 1/20
930/930 ━━━━━━━━━━━━━━━━━━━━ 14s 12ms/step - accuracy: 0.7518 - loss: 0.5826 - val_accuracy: 0.3054 - val_loss: 1.1537
Epoch 2/20
930/930 ━━━━━━━━━━━━━━━━━━━━ 11s 12ms/step - accuracy: 0.7981 - loss: 0.5209 - val_accuracy: 0.3054 - val_loss: 0.9798
Epoch 3/20
930/930 ━━━━━━━━━━━━━━━━━━━━ 11s 12ms/step - accuracy: 0.7890 - loss: 0.5056 - val_accuracy: 0.3054 - val_loss: 1.1210
Epoch 4/20
930/930 ━━━━━━━━━━━━━━━━━━━━ 11s 12ms/step - accuracy: 0.8226 - loss: 0.4259 - val_accuracy: 0.3290 - val_loss: 1.9482
Epoch 5/20
930/930 ━━━━━━━━━━━━━━━━━━━━ 10s 11ms/step - accuracy: 0.8604 - loss: 0.3517 - val_accuracy: 0.3806 - val_loss: 1.7019
Epoch 6/20
930/930 ━━━━━━━━━━━━━━━━━━━━ 11s 11ms/step - accuracy: 0.8834 - loss: 0.2851 - val_accuracy: 0.4172 - val_loss: 1.7682
Epoch 7/20
930/930 ━━━━━━━━━━━━━━━━━━━━ 10s 11ms/step - accuracy: 0.8775 - loss: 0.2766 - val_accuracy: 0.3785 - val_loss: 2.6785
Epoch 8/20
930/930 ━━━━━━━━━━━━━━━━━━━━ 10s 11ms/step - accuracy: 0.8940 - loss: 0.2480 - 

In [41]:
predictions = model.predict(X)
predictions

73/73 ━━━━━━━━━━━━━━━━━━━━ 1s 5ms/step


array([[0.7392194 ],
       [0.99999243],
       [0.7415817 ],
       ...,
       [0.99992883],
       [0.99898773],
       [0.00477201]], dtype=float32)

In [42]:
predictions.size

2324

In [43]:
binary_predictions = (predictions > 0.5).astype(int) # convert the predictions to binary
print(binary_predictions)


[[1]
 [1]
 [1]
 ...
 [1]
 [1]
 [0]]


In [52]:
from sklearn.metrics import classification_report, accuracy_score

# Calculate and print the accuracy score
accuracy = accuracy_score(df['NegoOutcomeLabel'], binary_predictions)
print(f'Accuracy: {accuracy:.4f}')

#Calculate average weighted f1 score
f1 = classification_report(df['NegoOutcomeLabel'], binary_predictions, output_dict=True)['weighted avg']['f1-score']
print(f'F1 Score: {f1:.4f}')



Accuracy: 0.8352
F1 Score: 0.8180


In [53]:
# Create a DataFrame for the current RNN model results
results_rnn = pd.DataFrame({
    'Model': ['RNN'],
    'Accuracy': [accuracy],
    'F1 Score': [f1]
})

In [44]:
from sklearn.metrics import classification_report

print(classification_report(df['NegoOutcomeLabel'], binary_predictions))

              precision    recall  f1-score   support

           0       0.94      0.50      0.66       725
           1       0.81      0.99      0.89      1599

    accuracy                           0.84      2324
   macro avg       0.88      0.74      0.77      2324
weighted avg       0.85      0.84      0.82      2324



In [47]:

# Generate the classification report
classification_report_dict = classification_report(df['NegoOutcomeLabel'], binary_predictions, output_dict=True)

# Convert the classification report to a DataFrame
classification_report_df = pd.DataFrame(classification_report_dict).transpose()


In [48]:
classification_report_df

precision    recall  f1-score      support
0              0.943005  0.502069  0.655266   725.000000
1              0.813725  0.986241  0.891716  1599.000000
accuracy       0.835198  0.835198  0.835198     0.835198
macro avg      0.878365  0.744155  0.773491  2324.000000
weighted avg   0.854056  0.835198  0.817953  2324.000000

In [55]:
results_rnn

Model  Accuracy  F1 Score
0   RNN  0.835198  0.817953

# RNN